---

# S05E05 : Deeper into classes & OOP - héritage complexe

Cyril Desjouy

--- 

## 1. Introduction

Nous avons vu dans le notebook précédent l'héritage simple. Python supporte également des schémas d'héritage plus complexes. En POO, il existe 5 types d'héritage qui sont schématisés ci-dessous et supportés par Python:

* ***Single inheritance:*** *A single class inherits from another.*
```                                            
                            ┌──────────────┐       ┌──────────────┐
                            │  Base class  ╞═══>═══╡   Subclass   │
                            └──────────────┘       └──────────────┘
``` 
* ***Multilevel inheritance:*** *One class inherits from another which in turn inherit from another...*

```                                            
                   ┌──────────────┐       ┌──────────────┐       ┌──────────────┐
                   │  Base class  ╞═══>═══╡   Subclass   ╞═══>═══╡   Subclass   │     
                   └──────────────┘       └──────────────┘       └──────────────┘
``` 
* ***Hierarchical inheritance:*** *More than one class inherits from a base class.*
```
                                                   ┌──────────────┐
                                          ╔════>═══╡   Subclass   |
                            ┌─────────────╨┐       └──────────────┘
                            │  Base class  │       
                            └─────────────╥┘       ┌──────────────┐
                                          ╚════>═══╡   Subclass   |
                                                   └──────────────┘
```     
* ***Multiple inheritance:*** *One class inherits from multiple classes.*

```
                            ┌──────────────┐
                            |  Base class  ╞═════>════╗
                            └──────────────┘         ┌╨─────────────┐
                                                     │  Base class  │ 
                            ┌──────────────┐         └╥─────────────┘
                            |  Base class  ╞═════>════╝
                            └──────────────┘
``` 
* ***Hybrid inheritance:*** *It is a combination of at least two kind of inheritance.*



## 2. L'algorithme ***mro***

Lorsqu'une classe hérite de plusieurs classes, il s'agit de déterminer dans quel ordre se fait l'héritage. Pour ce faire, Python utilise un algorithme appelé ***mro*** pour ***Multiple Resolution Order*** qui s'occupe de ça pour nous.

Pour illustrer ce concept, considérons la classe de base suivante:

In [4]:
class Animal:
    legs = 4
    
    @classmethod
    def count_legs(cls):
        print(cls.legs, 'legs')

La sortie du ***mro()*** de cette classe est la suivante:
```
>> Animal.mro()
[__main__.Animal, object]
```
Cette objet liste l'ordre dans lequel la résolution des attributs doit s'effectuer lors de l'héritage. Lorsque l'interpréteur Python recherche un attribut, il recherche tout d'abord dans le premier ***namespace*** listé par ***mro()***. S'il ne le trouve pas dans ce ***namespace***, il le cherche alors dans le suivant, et ainsi de suite. 

Considérons maintenant l'**héritage multi-niveaux** (***multilevel inheritance***) suivant:

In [5]:
class Turtle(Animal):
    attribute = 'shell'
    
class NinjaTurtle(Turtle):
    legs = 2

Les résultats des ***mro()*** pour chacune des sous-classes sont les suivants:
```python
>> Turtle.mro()
[__main__.Turtle, __main__.Animal, object]
>> NinjaTurtle.mro()
[__main__.NinjaTurtle, __main__.Turtle, __main__.Animal, object]
```

Lorsque la méthode `count_legs` est appelée depuis la sous-classe `Turtle`, l'interpréteur Python cherche dans le ***namespace*** de `Turtle` une méthode nommée `count_legs`, mais il ne la trouve pas. Il consulte alors le ***mro*** et cherche dans le ***namespace*** suivant, celui de `Animal` où il trouve `count_legs`.

Lorsque la méthode `count_legs` est appelée depuis la sous-classe `NinjaTurtle`, l'interpréteur Python cherche dans le ***namespace*** de `Turtle` une méthode nommée `count_legs`, mais il ne la trouve pas. Il consulte alors le ***mro*** et cherche dans le ***namespace*** suivant, celui de `Turtle` où il ne la trouve pas non plus. Il finit par trouver `count_legs` dans le ***namespace*** suivant, celui de `Animal`.

`Turtle` et `NinjaTurle` héritent donc tous deux de la méthode de classe `count_legs` définie dans la classe de base `Animal`: 
```python
>> Animal.count_legs()           # Returns 4
>> Turtle.count_legs()           # Returns 4
>> NinjaTurtle.count_legs()      # Returns 2
```
La même procédure est appliquée à l'attribut de classe `legs`. À l'appel de `count_legs` depuis `Turtle`, l'interpréteur Python cherche dans le ***namespace*** courrant `legs` mais ne le trouve pas. Il cherche dans le ***namespace*** suivant, celui de `Animal` où il le trouve. De la même manière, à l'appel de `count_legs` depuis `NinjaTurle`, l'interpréteur Python cherche dans le ***namespace*** courrant et trouve `legs`.

Dans ce cas simple, il n'y a pas vraiment d'ambiguïté. `NinjaTurle` hérite de `Turtle` qui hérite de `Animal` (qui hérite de `object`), mais dans des cas plus complexes, il faudra se référer au ***mro*** qui conditionne la recherche d'attributs dans la hiérarchie des classes qu'il définit. 

## 2. ***super(subclass, instance of the subclass)***

Nous avons vu dans le notebook précédent comment utiliser `super()` pour appeler une méthode d'une super-classe depuis une sous-classe. Nous l'avons alors utilisé sans argument. Il est également possible de lui fournir deux arguments d'entrée: 
```
super(subclass, instance of the subclass)
```
Dans le cas où `super()` est utilisé sans argument d'entrée, il prend par défaut la classe et l'instance courrantes. Dans le cas d'héritages complexes, il peut être intéressant de préciser quelle sous classe référencer pour pouvoir atteindre une classe particulière. Considérons l'**héritage multiple** suivant:

In [65]:
class Ninja:
    def __init__(self, weapon='nunchaku'):
        self.weapon = weapon
        
class Turtle:
    def __init__(self):
        self.armor = 'shell'
        
class NinjaTurtle(Ninja, Turtle):
    def __init__(self, weapon=None):
        super().__init__(weapon)           # Equivalent à super(NinjaTurtle, self).__init__(weapon)
        self.battlecry = 'cowabunga'

Dans le cas d'**héritage multiple**, les différentes classes de base sont simplement séparées par des virgules. Le résultat de ***mro()*** pour `NinjaTurtle` est le suivant:
```python
>> NinjaTurtle.mro()
[__main__.NinjaTurtle, __main__.Ninja, __main__.Turtle, object]
```

La méthode `__init__` de `Ninja` est appelée depuis la méthode `__init__` de `NinjaTurtle`. C'est en effet la première dans le ***mro()*** **après la classe courrante** (`NinjaTurtle`):
```python
>> donatello = NinjaTurtle(weapon='staff')
>> vars(donatello)
{'weapon': 'staff', 'battlecry': 'cowabunga'}
 ```
`NinjaTurtle` hérite bien de l'attribut d'instance `weapon` mais pas de `armor`. Pour qu'il récupère aussi les attributs d'instance de `Turtle`, il faut utiliser à nouveau `super`:

In [69]:
class NinjaTurtle(Ninja, Turtle):
    def __init__(self, weapon=None):
        super(NinjaTurtle, self).__init__(weapon)   # Equivalent to Ninja.__init__(self, weapon)
        super(Ninja, self).__init__()               # Equivalent to Turtle.__init__(self)
        self.battlecry = 'cowabunga'

`NinjaTurtle` est alors initialisé avec la méthode `__init__` de  `Ninja` puis celle de `Turtle` et récupère ainsi les attributs d'instance déclarés dans ces méthodes:
```python
>> donatello = NinjaTurtle(weapon='staff')
>> vars(donatello)
{'weapon': 'staff', 'armor': 'shell', 'battlecry': 'cowabunga'}
```
Vous noterez que la classe fournit en argument d'entrée de `super()` doit être la classe qui précède selon `mro()` la classe à atteindre.

## Quizz

<div class="alert alert-block alert-info">
Sans implémenter les classes suivantes, essayez de déterminer grâce aux résultats des mro():
    <ul>
    <li> Que vaut l'attribut <code>armor</code> dans <code>NinjaTurtle1</code> ? dans <code>NinjaTurtle2</code> ? </li>
    <li> Que vaut l'attribut <code>weapon</code> dans <code>NinjaTurtle1</code> ? dans <code>NinjaTurtle2</code> ?</li>
    </ul>
</div>

```python
class Human:
    weapon = 'intelligence'
    armor = 'clothes'
    
class Animal:
    weapon = 'instinct'
    
class Ninja(Human):
    weapon = 'nunchaku'
    
class Turtle(Animal):
    armor = 'shell'
    
class NinjaTurtle1(Ninja, Turtle):
    pass

class NinjaTurtle2(Turtle, Ninja):
    pass
```


```python
>> NinjaTurtle1.mro()
[__main__.NinjaTurtle1,
 __main__.Ninja,
 __main__.Human,
 __main__.Turtle,
 __main__.Animal,
 object]

>> NinjaTurtle2.mro()
[__main__.NinjaTurtle2,
 __main__.Turtle,
 __main__.Animal,
 __main__.Ninja,
 __main__.Human,
 object]
```